# Get papers & journals by Scopus authors

This 

In [1]:
from scopus import ScopusSearch
import pandas as pd
import time
import requests
import xml.etree.ElementTree as ElementTree
import re

C:\Users\Rekaroge\Anaconda3\lib\site-packages\socks.py:58: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  from collections import Callable


In [36]:
pd.set_option('display.max_colwidth', -1)
pd.set_option('display.max_rows', 500)

In [2]:
def getText(elem):
    ''' 
    Get the text from the XML response and return a string.
    '''
    try:
        msg = elem.text  
        msg = msg.replace('<br>', '')
    except:
        msg = ""

    if msg is None:
        msg = "not available"

    return msg

In [3]:
def searchOpenURL(row):
    '''(pandas.DataFrame) --> pandas.Series
    
    This function takes a row of a pandas DataFram and gets the ISSN of a journal. When used with the pandas apply function, this function uses the ISSNs to run a HTTP query against a library OpenURL link resolver server, retrieves the XML response, and parses out the package name and coverage dates. Using getText, this function returns two columns in a panda Series for each row: a statement of availability, and a statement of coverage (package names and the dates they cover).
    
    '''
    # Create and run an HTTP request against the open URL link resolver 
    r = requests.get('http://na01.alma.exlibrisgroup.com/view/uresolver/01UTON_UW/openurl?svc_dat=CTO&issn={}'.format(row['q_issn']))
    # Parse the XML response and store it as root
    root = ElementTree.fromstring(r.content)
    # Create a dict of namespace values for use later on, so that the queries of the stored XML response can be cleaner
    ns = {'resolver': 'http://com/exlibris/urm/uresolver/xmlbeans/u'}
    # Create an empty dict that will be used to store the coverage statements for each journal. Key will be the package name, value will be the coverage dates.
    coverage_statement = {}
    
    # get all full-text services
    
    # if there is a full-text service
    if root.findall('.//resolver:context_service[@service_type="getFullTxt"]',ns) != []:
        # set the availability statement to show that there is a full-text
        avail_statement = 'Full-text available'
        print('Full-text available for ' + row['q_issn'])
        # for each full-text service
        for service in root.findall('.//resolver:context_service[@service_type="getFullTxt"]',ns):
            # Create empty str variables to store the details of the full-text service
            servicePackageName = ''
            serviceCoverage = ''
            # get package name of the full-text service and add it to the temporary str variable
            package = service.find('.//resolver:key[@id="package_public_name"]',ns)
            servicePackageName = getText(package)
            
            # get coverage date statement of the full-text service and add it to the temptorary str variable
            avail = service.find('.//resolver:key[@id="Availability"]',ns)
            serviceCoverage = getText(avail)
            # Add the details of this full-text service to the dict
            coverage_statement[servicePackageName] = serviceCoverage
    # When there is no full-text service
    else:
        # set the availability statement to show that there is no full-text
        avail_statement = 'No full-text available'
        print('Full-text not available for ' + row['q_issn'])
    # Return the availability and coverage statements as a pandas Series
    return pd.Series([avail_statement, coverage_statement])

In [4]:
def coverageStatement_availParser(row):
    '''
    (pd.Series) -> pd.Series
    
    This function parses out info from the coverage statements for all packages, and updates the availability statements for the journals to reflect those journals that don't have full-text coverage, those that do up to the present, those with embargo and those with full-text access, but not to the present.
    
    '''
    # Create an empy str for the coverage statement value
    avail_statement = ''
    # Only do run this function if there are full-text resources
    if row['coverage'] != {}:
        # Create an empty variable that will change if the function should stop
        stop = 0
        # Check all coverage statements in the dict, and if any ONE of them doesn't contain the words 'most recent' or 'until' (i.e., its up to the current), set the availability statement to available to present and stop.
        for value in row['coverage'].values():
            # Skip values that don't contain any data
            if value != '':
                if not any(s in value for s in ('Most recent', 'until')):
                    avail_statement = 'Full-text available to present'
                    stop = 1
                    break
        # If there was no coverage statement where there was full-text to the present, continue
        if stop == 0:
            for value in row['coverage'].values():
                if value != '':
                    # If there is any ONE line coverage statement that is for an embargo
                    if 'Most recent' in value:
                        avail_statement = 'Full-text available with embargo'
                        stop = 1
                        break
        # If there is no statement up to the present, nor for an embargo, then it must be available, but not complete.
        if stop == 0:
            for value in row['coverage'].values():
                if value != '':
                    if 'until' in value:
                        avail_statement = 'Full-text available, but not complete'
    else:
        avail_statement = 'No full-text available'
    return pd.Series([avail_statement])

In [32]:
def coverageStatement_yearsParser(row):
    '''
    (pd.Series) -> pd.Series
    
    This function takes the coverage statements provided by the link resolver, parses out the dates, and creates a one line date range of coverage.
    '''
    
    tempList = []
    # Don't do this if there are no coverage statements
    if row['coverage'] != {}:
        # iterate over every statement in the dict 
        for value in row['coverage'].values():
            # Only do this if the coverage statement has data on the date coverage
            if 'Available from' in value:
                # For coverage statements to the present
                if not any(s in value for s in ('Most recent', 'until')):
                    tempList.append((re.search(r"Available from (\d{4})", value).group(1)) + ' - present')
                # For coverage statements with an embargo
                if 'Most recent' in value:
                    tempList.append((re.search(r"Available from (\d{4})", value).group(1))  + ' - ' + re.search(r'Most recent (.*?)\(s\)', value).group(1) + ' ago')
                # For coverage statements that aren't current to the present
                if 'until' in value:
                    tempList.append((re.search(r"Available from (\d{4})", value).group(1)) + ' - ' + (re.search(r"until (\d{4})", value).group(1)))
    return pd.Series([tempList])

In [29]:
# Start a timer
start_time = time.time()

# Import list of researchers as a dataframe
df_facultyMembers = pd.read_csv('Data/researchers.csv')

In [6]:
# Create an empty list for author Scopus IDs
authors = []

# Populate list with Scopus IDs from the facutly member dataframe
for scopusID in df_facultyMembers['scopusID']:
    authors.append(scopusID)

In [7]:
# Create the query of Scopus IDs that will be used in the API call
# Create an empty string
query = ''
# Add every Scopus ID to the string except for the last one, because the query command must not end with "OR"
for author in authors[:-1]:
    query = query + 'AU-ID(' + str(author) + ') OR '
# Add the last Scopus ID  
query = query + 'AU-ID(' + str(authors[-1]) + ')'

In [8]:
# Search the Scopus API for all publications by these authors, in one search
s = ScopusSearch('{}'.format(query), refresh=True, subscriber=True)

In [9]:
print("--- %s seconds ---" % (time.time() - start_time))

--- 61.955257177352905 seconds ---


In [10]:
# Convert API results into a dataframe
df = pd.DataFrame(pd.DataFrame(s.results))

In [11]:
# Convert appropriate data into ints
df["citedby_count"] = pd.to_numeric(df["citedby_count"])
df["openacess"] = pd.to_numeric(df["openaccess"])
df["author_count"] = pd.to_numeric(df["author_count"])

In [12]:
# Add number of times a journal has been published in
df['count'] = df.groupby('source_id')['source_id'].transform('count')

In [37]:
df

eid  \
0     2-s2.0-85064014829   
1     2-s2.0-85065527826   
2     2-s2.0-85065401518   
3     2-s2.0-85063386854   
4     2-s2.0-85063729352   
5     2-s2.0-85059859084   
6     2-s2.0-85062851819   
7     2-s2.0-85066327778   
8     2-s2.0-85064043149   
9     2-s2.0-85061345149   
10    2-s2.0-85065017336   
11    2-s2.0-85066294758   
12    2-s2.0-85062345650   
13    2-s2.0-85065404432   
14    2-s2.0-85065318070   
15    2-s2.0-85058684846   
16    2-s2.0-85062801977   
17    2-s2.0-85048985395   
18    2-s2.0-85064514324   
19    2-s2.0-85062659789   
20    2-s2.0-85064594707   
21    2-s2.0-85064196102   
22    2-s2.0-85062617534   
23    2-s2.0-85058688830   
24    2-s2.0-85059128532   
25    2-s2.0-85062195624   
26    2-s2.0-85053499511   
27    2-s2.0-85062267616   
28    2-s2.0-85061497982   
29    2-s2.0-85059888486   
30    2-s2.0-85058018233   
31    2-s2.0-85051406123   
32    2-s2.0-85066108572   
33    2-s2.0-85065074084   
34    2-s2.0-85055905430   
35    2-s2.0-85054897756   
36    2-s2.0-85062447166   
37    2-s2.0-85065290885   
38    2-s2.0-85061506027   
39    2-s2.0-85059849478   
40    2-s2.0-85059829221   
41    2-s2.0-85055741365   
42    2-s2.0-85061755352   
43    2-s2.0-85064492826   
44    2-s2.0-85056161294   
45    2-s2.0-85062784071   
46    2-s2.0-85064189564   
47    2-s2.0-85061666426   
48    2-s2.0-85066015650   
49    2-s2.0-85064689293   
50    2-s2.0-85065183759   
51    2-s2.0-85058948600   
52    2-s2.0-85055494306   
53    2-s2.0-85053217906   
54    2-s2.0-85056446746   
55    2-s2.0-85057953501   
56    2-s2.0-85051732268   
57    2-s2.0-85055251352   
58    2-s2.0-85047378596   
59    2-s2.0-85051678691   
60    2-s2.0-85055029700   
61    2-s2.0-85053061957   
62    2-s2.0-85049569313   
63    2-s2.0-85056784301   
64    2-s2.0-85048592923   
65    2-s2.0-85052102675   
66    2-s2.0-85055074079   
67    2-s2.0-85053070260   
68    2-s2.0-85052299863   
69    2-s2.0-85051250888   
70    2-s2.0-85013827367   
71    2-s2.0-85048986159   
72    2-s2.0-85047464470   
73    2-s2.0-85051065278   
74    2-s2.0-85057248838   
75    2-s2.0-85054819944   
76    2-s2.0-85053046402   
77    2-s2.0-85054730823   
78    2-s2.0-85046403778   
79    2-s2.0-85050197158   
80    2-s2.0-85042167510   
81    2-s2.0-85044140701   
82    2-s2.0-85048499004   
83    2-s2.0-85047190733   
84    2-s2.0-85051211964   
85    2-s2.0-85044854992   
86    2-s2.0-85040254054   
87    2-s2.0-85046694024   
88    2-s2.0-85047274905   
89    2-s2.0-85044374674   
90    2-s2.0-85034569534   
91    2-s2.0-85046627382   
92    2-s2.0-85038213024   
93    2-s2.0-85047149307   
94    2-s2.0-85041086730   
95    2-s2.0-85045734365   
96    2-s2.0-85044852810   
97    2-s2.0-85044606703   
98    2-s2.0-85044259459   
99    2-s2.0-85043996179   
100   2-s2.0-85032839381   
101   2-s2.0-85044376818   
102   2-s2.0-85027696728   
103   2-s2.0-85030677375   
104   2-s2.0-85041621742   
105   2-s2.0-85040841021   
106   2-s2.0-85056564919   
107   2-s2.0-85032786861   
108   2-s2.0-85052531828   
109   2-s2.0-85053633096   
110   2-s2.0-85053617006   
111   2-s2.0-85052296831   
112   2-s2.0-85037748576   
113   2-s2.0-85024405475   
114   2-s2.0-85052865765   
115   2-s2.0-85036494884   
116   2-s2.0-85034023693   
117   2-s2.0-85034589406   
118   2-s2.0-85042503416   
119   2-s2.0-85056565717   
120   2-s2.0-85058653500   
121   2-s2.0-85038030964   
122   2-s2.0-85037618216   
123   2-s2.0-85040118031   
124   2-s2.0-85044049299   
125   2-s2.0-85027966365   
126   2-s2.0-85029721479   
127   2-s2.0-85033558511   
128   2-s2.0-85035811262   
129   2-s2.0-85028472192   
130   2-s2.0-85038235441   
131   2-s2.0-85038222291   
132   2-s2.0-85013482394   
133   2-s2.0-85028961248   
134   2-s2.0-85031767727   
135   2-s2.0-85023635573   
136   2-s2.0-85030441835   
137   2-s2.0-85018727924   
138   2-s2.0-85024488570   
139   2-s2.0-85020430683   
140   2-s2.0-85028603926   
141   2-s2.0-85038432244   
142   2-s2.0-8501

In [14]:
# Create a new dataframe of journals, with duplicates of journals removed
df_journals = df.drop_duplicates('source_id')

In [15]:
# Get rid of unnessary columns
df_journals = df_journals[['publicationName','source_id', 'issn', 'eIssn', 'aggregationType', 'count']]

In [16]:
# Sort the dataframe by publication count
df_journals = df_journals.sort_values(by=['count'], ascending=False)

In [17]:
# Reset the index count for this dataframe
df_journals = df_journals.reset_index(drop=True)

In [18]:
# delete all rows where aggregate type is not a journal
indexNames = df_journals[df_journals['aggregationType'] != 'Journal'].index
df_journals.drop(indexNames, inplace=True)

# delete all rows where there is no source ID
indexNames = df_journals[df_journals.source_id.isnull()].index
df_journals.drop(indexNames, inplace=True)

# delete all rows where there is no ISSN and eISSN
indexNames = df_journals[df_journals.issn.isnull() & df_journals.eIssn.isnull()].index
df_journals.drop(indexNames , inplace=True)

In [19]:
# Create a column with an ISSN for searching, and populate with the values for the eISSN
df_journals['q_issn'] = df_journals['eIssn']

In [20]:
# For those rows where there is no eISSN, replace them with the ISSN
df_journals.loc[df_journals['q_issn'].isnull(),'q_issn'] = df_journals['issn']

In [21]:
df_journals

publicationName    source_id      issn  \
0                      Journal of Great Lakes Research        17510  03801330   
1    Canadian Journal of Fisheries and Aquatic Scie...        12016  0706652X   
2               Environmental Toxicology and Chemistry        25094  07307268   
3                                     Animal Behaviour        24580  00033472   
4                                 Biological Invasions        13257  13873547   
5                 Environmental Science and Technology        21537  0013936X   
6                                    Molecular Ecology        20297  09621083   
7                              Journal of Fish Biology        22560  00221112   
8                                        Hydrobiologia        15168  00188158   
9                                             PLoS ONE  10600153309      None   
10                     Journal of Evolutionary Biology        18920  1010061X   
11                                  Freshwater Biology        15112  00465070   
12                         Diversity and Distributions        14551  13669516   
13                               Ecology and Evolution  21100264002      None   
14                            Journal of Avian Biology        22035  09088857   
15                                  Behavioral Ecology        13151  10452249   
16                                         Chemosphere        24657  00456535   
17   Proceedings of the Royal Society B: Biological...       130030  09628452   
18                                            Ethology        21489  01791613   
19   Bulletin of Environmental Contamination and To...        24624  00074861   
20                                            Heredity        22235  0018067X   
21            International Journal of Hydrogen Energy        26991  03603199   
22                                           Oecologia        12925  00298549   
23                          Limnology and Oceanography        29576      None   
24                             Ecological Applications        20287      None   
25                      Marine Ecology Progress Series        12169  01718630   
26                         Canadian Journal of Zoology        24765  00084301   
27                               Conservation Genetics        22069  15660621   
28                    Science of the Total Environment        25349  00489697   
29                                           Behaviour        24713  00057959   
..                                                 ...          ...       ...   
390                                    Acta Ethologica        24090  08739749   
391                                   Animal Cognition        29520  14359448   
392                      Journal of Crustacean Biology        22543  02780372   
393  Journal of the Canadian Society of Forensic Sc...        12426  00085030   
395                             Brain Research Reviews        14351  01650173   
396                                    Plant Pathology        16614  00320862   
397                      Marine Environmental Research        24021  01411136   
399                                  Antarctic Science        13040  09541020   
400                                       ISME Journal   5800173382  17517362   
401                             Journal of Herpetology        22562  00221511   
402                    Current Opinion in Neurobiology        14992  09594388   
403                                          Zebrafish       130177  15458547   
404                                         Oncotarget  19900191708      None   
405                             Molecular Neurobiology        14160  08937648   
406                         Ecology of Freshwater Fish        21449  09066691   
407                                             Arctic        19348  00040843   
409                Limnology and Oceanography: Methods   4400151737      None   
410               Clinical and Experimental Metastasis        29256  0

In [22]:
# Search the Open URL link resolver to find the coverage for these journals
df_journals[['availability', 'coverage']] = df_journals.apply(searchOpenURL ,axis=1)

Full-text available for 03801330
Full-text available for 03801330
Full-text available for 12057533
Full-text available for 15528618
Full-text available for 00033472
Full-text available for 15731464
Full-text available for 15205851
Full-text available for 1365294X
Full-text available for 10958649
Full-text available for 15735117
Full-text available for 19326203
Full-text available for 14209101
Full-text available for 13652427
Full-text available for 14724642
Full-text available for 20457758
Full-text available for 1600048X
Full-text available for 14657279
Full-text available for 18791298
Full-text available for 14712954
Full-text available for 14390310
Full-text available for 14320800
Full-text available for 13652540
Full-text available for 03603199
Full-text available for 00298549
Full-text available for 19395590
Full-text available for 19395582
Full-text available for 01718630
Full-text available for 00084301
Full-text available for 15729737
Full-text available for 18791026
Full-text 

Full-text available for 00099120
Full-text available for 14320983
Full-text available for 0379864X
Full-text available for 03043770
Full-text available for 11758805
Full-text not available for 00770825
Full-text available for 14698714
Full-text available for 10970029
Full-text available for 01689525
Full-text available for 01427873
Full-text available for 20457758
Full-text available for 09258574
Full-text available for 14322048
Full-text not available for 00431370
Full-text available for 07302312
Full-text available for 15253961
Full-text available for 09218181
Full-text available for 09254773
Full-text available for 08926638
Full-text available for 14442906
Full-text available for 07349750
Full-text available for 09291903
Full-text available for 10728368
Full-text available for 00144827
Full-text available for 0006291X
Full-text available for 13861980
Full-text available for 10889051
Full-text available for 10689265
Full-text available for 07308000
Full-text not available for 2530064

In [25]:
# Update the availability statements based on the coverage dates (emabargo, not to the present)
df_journals[['availability']] = df_journals.apply(coverageStatement_availParser,axis=1)

In [33]:
# Create a column of just the date ranges for the journals
df_journals[['coverageRange']] = df_journals.apply(coverageStatement_yearsParser,axis=1)

In [34]:
df_journals.availability.value_counts()

Full-text available to present           327
Full-text available with embargo         24 
No full-text available                   19 
Full-text available, but not complete    19 
Name: availability, dtype: int64

In [38]:
df_journals

publicationName  \
0    Journal of Great Lakes Research                                                                  
1    Canadian Journal of Fisheries and Aquatic Sciences                                               
2    Environmental Toxicology and Chemistry                                                           
3    Animal Behaviour                                                                                 
4    Biological Invasions                                                                             
5    Environmental Science and Technology                                                             
6    Molecular Ecology                                                                                
7    Journal of Fish Biology                                                                          
8    Hydrobiologia                                                                                    
9    PLoS ONE                                                                                         
10   Journal of Evolutionary Biology                                                                  
11   Freshwater Biology                                                                               
12   Diversity and Distributions                                                                      
13   Ecology and Evolution                                                                            
14   Journal of Avian Biology                                                                         
15   Behavioral Ecology                                                                               
16   Chemosphere                                                                                      
17   Proceedings of the Royal Society B: Biological Sciences                                          
18   Ethology                                                                                         
19   Bulletin of Environmental Contamination and Toxicology                                           
20   Heredity                                                                                         
21   International Journal of Hydrogen Energy                                                         
22   Oecologia                                                                                        
23   Limnology and Oceanography                                                                       
24   Ecological Applications                                                                          
25   Marine Ecology Progress Series                                                                   
26   Canadian Journal of Zoology                                                                      
27   Conservation Genetics                                                                            
28   Science of the Total Environment                                                                 
29   Behaviour                                                                                        
30   Bioacoustics                                                                                     
31   Aquaculture                                                                                      
32   Journal of Ornithology                                                                           
33   Transactions of the American Fisheries Society                                                   
34   Journal of Experimental Biology                                                                  
35   Auk                                                                                              
36   Environmental Pollution                                                                          
37   Behavioral Ecology and Sociobiology                                                              
38   Journal of Comparative Physiology A: Neuroethology, Sensory, N

In [42]:
df_journals[df_journals['availability'] == 'No full-text available']

publicationName    source_id      issn  \
108  Marine and Freshwater Research              27846        13231650   
128  Archiv fur Hydrobiologie                    13046        00039136   
156  Fundamental and Applied Limnology           5400152636   18639135   
166  Emu                                         21574        01584197   
172  British Phycological Journal                67985        00071617   
175  Zootaxa                                     4700151916   11755326   
207  Oceanological Studies                       66993        1505232X   
218  Progress in cell cycle research             19022        10872957   
221  American Fisheries Society Symposium        29410        08922284   
235  Canadian Acoustics - Acoustique Canadienne  12971        07116659   
242  Nature Ecology and Evolution                21100831440  None       
250  Chinese Journal of Biomedical Engineering   21456        02588021   
266  Monographs in developmental biology         96436        00770825   
276  Water Resources Bulletin                    39598        00431370   
293  Perspectives in Ecology and Conservation    21100817643  25300644   
318  Bioscience Education                        21100220137  None       
353  Journal of Insects as Food and Feed         21100830759  None       
378  International Journal on Algae              19130        15219429   
420  Iranian Journal of Fisheries Sciences       19900193543  15622916   

        eIssn aggregationType  count    q_issn            availability  \
108  None      Journal         3.0    13231650  No full-text available   
128  None      Journal         3.0    00039136  No full-text available   
156  None      Journal         2.0    18639135  No full-text available   
166  None      Journal         2.0    01584197  No full-text available   
172  None      Journal         2.0    00071617  No full-text available   
175  11755334  Journal         2.0    11755334  No full-text available   
207  None      Journal         1.0    1505232X  No full-text available   
218  None      Journal         1.0    10872957  No full-text available   
221  None      Journal         1.0    08922284  No full-text available   
235  None      Journal         1.0    07116659  No full-text available   
242  2397334X  Journal         1.0    2397334X  No full-text available   
250  None      Journal         1.0    02588021  No full-text available   
266  None      Journal         1.0    00770825  No full-text available   
276  None      Journal         1.0    00431370  No full-text available   
293  None      Journal         1.0    25300644  No full-text available   
318  14797860  Journal         1.0    14797860  No full-text available   
353  23524588  Journal         1.0    23524588  No full-text available   
378  None      Journal         1.0    15219429  No full-text available   
420  None      Journal         1.0    15622916  No full-text available   

    coverage coverageRange  
108  {}       []            
128  {}       []            
156  {}       []            
166  {}       []            
172  {}       []            
175  {}       []            
207  {}       []            
218  {}       []            
221  {}       []            
235  {}       []            
242  {}       []            
250  {}       []            
266  {}       []            
276  {}       []            
293  {}       []            
318  {}       []            
353  {}       []            
378  {}       []            
420  {}       []

In [44]:
df_journals[df_journals['availability'] == 'Full-text available with embargo']

publicationName    source_id  \
17   Proceedings of the Royal Society B: Biological Sciences  130030        
34   Journal of Experimental Biology                          29605         
50   Physiological and Biochemical Zoology                    23318         
51   American Naturalist                                      12604         
62   Journal of Neuroscience                                  16764         
76   Biology Letters                                          145678        
87   Journal of Cell Biology                                  18555         
94   Freshwater Science                                       21100297824   
149  Plant Physiology                                         16615         
151  Cancer Research                                          29183         
157  Blood                                                    25454         
174  Canadian Field-Naturalist                                20071         
206  Molecular Biology of the Cell                            18605         
237  Oncogene                                                 12523         
282  FASEB Journal                                            15048         
285  Cancer Gene Therapy                                      29127         
294  Endocrine-Related Cancer                                 26035         
299  Journal of Water and Health                              17512         
356  Cancer Cell                                              29093         
369  Journal of the Royal Society Interface                   4000151907    
374  Plant Disease                                            60195         
379  International Journal of Developmental Biology           29499         
400  ISME Journal                                             5800173382    
407  Arctic                                                   19348         

         issn     eIssn aggregationType  count    q_issn  \
17   09628452  14712954  Journal         13.0   14712954   
34   00220949  None      Journal         9.0    00220949   
50   15222152  None      Journal         7.0    15222152   
51   00030147  None      Journal         7.0    00030147   
62   02706474  15292401  Journal         5.0    15292401   
76   17449561  1744957X  Journal         4.0    1744957X   
87   00219525  15408140  Journal         4.0    15408140   
94   21619549  21619565  Journal         3.0    21619565   
149  00320889  None      Journal         2.0    00320889   
151  00085472  None      Journal         2.0    00085472   
157  00064971  None      Journal         2.0    00064971   
174  00083550  None      Journal         2.0    00083550   
206  10591524  None      Journal         1.0    10591524   
237  09509232  None      Journal         1.0    09509232   
282  08926638  None      Journal         1.0    08926638   
285  09291903  None      Journal         1.0    09291903   
294  13510088  14796821  Journal         1.0    14796821   
299  14778920  None      Journal         1.0    14778920   
356  15356108  18783686  Journal         1.0    18783686   
369  17425689  17425662  Journal         1.0    17425662   
374  01912917  None      Journal         1.0    01912917   
379  02146282  None      Journal         1.0    02146282   
400  17517362  17517370  Journal         1.0    17517370   
407  00040843  19231245  Journal         1.0    19231245   

                         availability  \
17   Full-text available with embargo   
34   Full-text available with embargo   
50   Full-text available with embargo   
51   Full-text available with embargo   
62   Full-text available with embargo   
76   Full-text available with embargo   
87   Full-text available with embargo   
94   Full-text available with embargo   
149  Full-text available with embargo   
151  Full-text available with embargo   
157  Full-text available with embargo   
174  Full-text available with embargo   
206  Full-text available with embargo   
237  Full-text available with embargo   
282

In [45]:
df_journals[df_journals['availability'] == 'Full-text available, but not complete']

publicationName  \
25   Marine Ecology Progress Series                                                          
59   Ornitologia Neotropical                                                                 
61   Molecular Ecology Notes                                                                 
144  Journal of Neurocytology                                                                
159  Developmental Genetics                                                                  
160  Brain, Behavior and Evolution                                                           
161  Developmental Brain Research                                                            
167  Journal of the North American Benthological Society                                     
222  Journal of Experimental Zoology Part B: Molecular and Developmental Evolution           
253  Mutation Research - Environmental Mutagenesis and Related Subjects                      
286  Nature Structural Biology                                                               
289  Journal of Aquatic Ecosystem Stress and Recovery                                        
298  Biochimica et Biophysica Acta - Protein Structure and Molecular Enzymology              
304  Comparative Biochemistry and Physiology - C Pharmacology Toxicology and Endocrinology   
317  Journal of Environmental Quality                                                        
383  Agronomy Journal                                                                        
386  Journal of Computational Biology                                                        
395  Brain Research Reviews                                                                  
403  Zebrafish                                                                               

       source_id      issn     eIssn aggregationType  count    q_issn  \
25   12169        01718630  None      Journal         12.0   01718630   
59   4700152417   10754377  None      Journal         5.0    10754377   
61   20299        14718278  14718286  Journal         5.0    14718286   
144  18573        03004864  None      Journal         2.0    03004864   
159  38446        0192253X  None      Journal         2.0    0192253X   
160  14323        00068977  None      Journal         2.0    00068977   
161  15034        01653806  None      Journal         2.0    01653806   
167  12904        08873593  None      Journal         2.0    08873593   
222  22556        0022104X  None      Journal         1.0    0022104X   
253  31756        01651161  None      Journal         1.0    01651161   
286  39845        10728368  None      Journal         1.0    10728368   
289  70809        13861980  None      Journal         1.0    13861980   
298  52056        01674838  None      Journal         1.0    01674838   
304  15300154800  07428413  None      Journal         1.0    07428413   
317  23375        00472425  15372537  Journal         1.0    15372537   
383  15639        00021962  14350645  Journal         1.0    14350645   
386  29581        10665277  None      Journal         1.0    10665277   
395  14351        01650173  None      Journal         1.0    01650173   
403  130177       15458547  None      Journal         1.0    15458547   

                              availability  \
25   Full-text available, but not complete   
59   Full-text available, but not complete   
61   Full-text available, but not complete   
144  Full-text available, but not complete   
159  Full-text available, but not complete   
160  Full-text available, but not complete   
161  Full-text available, but not complete   
167  Full-text available, but not complete   
222  Full-text available, but not complete   
253  Full-text available, but not complete   
286  Full-text available, but not complete   
289  Full-text available, but not complete   
298  Full-text available, but not complete   
304  Full-text available, but not complete   
317  Full-text available, but not complete 

In [47]:
df_journals.to_csv('Results/journals.csv')